In [1]:
%autosave 20

#basic library
import pandas as pd
import numpy as np
import collections
from collections import defaultdict


#model training
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler


# visulization
import matplotlib.pyplot as plt
import seaborn as sns
plt.style.use('seaborn')

# Data statistics
from scipy import stats



# print all the outputs in a cell
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"


pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

Autosaving every 20 seconds


In [2]:
df = pd.read_excel('DatabaseForFunction_2019_2021.xlsx', index_col=0, dtype={'fipsValue':'object'})

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11232 entries, 0 to 11231
Data columns (total 19 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   State                     11232 non-null  object        
 1   County                    11232 non-null  object        
 2   fipsValue                 11232 non-null  object        
 3   PDensity                  11232 non-null  float64       
 4   Population                11232 non-null  int64         
 5   Year                      11232 non-null  int64         
 6   Month                     11232 non-null  int64         
 7   SNAP_Applications         11232 non-null  int64         
 8   last_date_time            11232 non-null  datetime64[ns]
 9   date_time                 11232 non-null  datetime64[ns]
 10  last_snap                 11232 non-null  int64         
 11  last_worker               11232 non-null  int64         
 12  last_disaster     

In [4]:
df.columns.to_list()

['State',
 'County',
 'fipsValue',
 'PDensity',
 'Population',
 'Year',
 'Month',
 'SNAP_Applications',
 'last_date_time',
 'date_time',
 'last_snap',
 'last_worker',
 'last_disaster',
 'last_google_calfresh',
 'last_google_food_bank',
 'last_google_food_pantry',
 'last_google_food_stamps',
 'last_google_supplemental',
 'last_google_snap']

## Pipeline to add columns / features
- dummy for state

## Columns adjust
Delete column ‘last_google_snap’ and ‘google_snap’ because of overlap meaning with google word ‘supplemental nutrition assistance program’
Add seasonal dummy variable
  - Summer: whether last month is 6/7/8
  - holiday: whether last month is 11/12

In [5]:
def addFeatures(df):
    
    # 1. dummy for State - split CA and texas using dummy

    # create dummy variables
    dummies = pd.get_dummies(df['State'], prefix='State')
    # concatenate the dummy variables with the original dataframe
    df = pd.concat([df, dummies], axis=1)
    # drop State_Texas since using dummy
    df = df.drop(columns='State_Texas')
    
    #2. Summer and holiday
    
    # find the idx of last_date_time
    idx_last_datetime = 0
    for i in range(len(df)):
        if df.columns[i] == 'last_date_time':
            idx_last_datetime = i
            print(i)
            break
            
    
    summer_month = [6, 7, 8]
    holiday_month = [11, 12]

    df['summer'] = 0    # idx= -2
    df['holiday'] = 0   # idx= -1

    for i in range(len(df)):
        if df.iloc[i,idx_last_datetime].month in summer_month: # 8 is the idx of last_date _time
            df.iloc[i, -2] = 1

        if df.iloc[i,idx_last_datetime].month in holiday_month:
            df.iloc[i, -1] = 1
    

    # 3. Delete columms related with google research work snap application
    if 'last_google_snap' in df.columns:
        df = df.drop(columns=['last_google_snap'])
        
    return df

In [6]:
df2 = addFeatures(df)

8


In [7]:
df2.head()

State          County fipsValue  PDensity  Population  Year  Month  \
0  California  Alameda County     06001    1898.5     1559308  2019      1   
1  California  Alameda County     06001    1898.5     1559308  2019      2   
2  California  Alameda County     06001    1898.5     1559308  2019      3   
3  California  Alameda County     06001    1898.5     1559308  2019      4   
4  California  Alameda County     06001    1898.5     1559308  2019      5   

   SNAP_Applications last_date_time  date_time  last_snap  last_worker  \
0               5515     2018-12-01 2019-01-01          0            0   
1               4478     2019-01-01 2019-02-01       5515           45   
2               5041     2019-02-01 2019-03-01       4478          397   
3               5253     2019-03-01 2019-04-01       5041          191   
4               8074     2019-04-01 2019-05-01       5253          808   

   last_disaster  last_google_calfresh  last_google_food_bank  \
0              0                  0.00                   0.00   
1              0                 24.00                  28.75   
2              0                 27.25                  27.75   
3              0                 19.60                  23.20   
4              0                 23.25                  22.50   

   last_google_food_pantry  last_google_food_stamps  last_google_supplemental  \
0                     0.00                     0.00                      0.00   
1                    38.00                    55.50                     54.50   
2                    38.75                    31.25                     36.75   
3                    33.80                    31.80                     35.20   
4                    35.50                    22.00                     29.25   

   State_California  summer  holiday  
0                 1       0        1  
1                 1       0        0  
2                 1       0        0  
3                 1       0        0  
4                 1       0        0

In [8]:
df2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11232 entries, 0 to 11231
Data columns (total 21 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   State                     11232 non-null  object        
 1   County                    11232 non-null  object        
 2   fipsValue                 11232 non-null  object        
 3   PDensity                  11232 non-null  float64       
 4   Population                11232 non-null  int64         
 5   Year                      11232 non-null  int64         
 6   Month                     11232 non-null  int64         
 7   SNAP_Applications         11232 non-null  int64         
 8   last_date_time            11232 non-null  datetime64[ns]
 9   date_time                 11232 non-null  datetime64[ns]
 10  last_snap                 11232 non-null  int64         
 11  last_worker               11232 non-null  int64         
 12  last_disaster     

In [9]:
# Build the model for predict
import statsmodels.api as sm
import pandas as pd


features = ['last_snap','last_worker','last_disaster','last_google_calfresh','last_google_food_bank','last_google_food_pantry','last_google_food_stamps','last_google_supplemental','State_California','summer','holiday','PDensity','Population']
target = ['SNAP_Applications']

X = df2[features]
y = df2[target]
    
# Add constant term to X
X = sm.add_constant(X)

# Fit linear regression model
model = sm.OLS(y, X).fit()

In [10]:
model.params

const                       225.555340
last_snap                     0.593283
last_worker                  -0.107813
last_disaster               318.219884
last_google_calfresh         -2.774608
last_google_food_bank         4.003876
last_google_food_pantry      -4.724196
last_google_food_stamps       7.960850
last_google_supplemental    -11.886163
State_California           -185.251893
summer                       42.794985
holiday                      86.879617
PDensity                     -0.174652
Population                    0.002745
dtype: float64

In [11]:
data_Jan_2022_last_snap = df2.loc[(df2.Month == 12) & (df2.Year == 2021)]

## Download 2019-2021 data

In [12]:
origin_data = pd.read_excel('dataForPrediction_2022.xlsx', index_col=0, dtype={'fipsValue':str})

In [13]:
origin_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3744 entries, 0 to 3743
Data columns (total 18 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   State                     3744 non-null   object        
 1   County                    3744 non-null   object        
 2   fipsValue                 3744 non-null   object        
 3   PDensity                  3744 non-null   float64       
 4   Population                3744 non-null   int64         
 5   Year                      3744 non-null   int64         
 6   Month                     3744 non-null   int64         
 7   last_date_time            3744 non-null   datetime64[ns]
 8   date_time                 3744 non-null   datetime64[ns]
 9   last_snap                 3744 non-null   int64         
 10  last_worker               3744 non-null   int64         
 11  last_disaster             3744 non-null   int64         
 12  last_google_calfresh

In [14]:
origin_data.head()

State          County fipsValue  PDensity  Population  Year  Month  \
0  California  Alameda County     06001    1898.5     1559308  2022      1   
1  California  Alameda County     06001    1898.5     1559308  2022      2   
2  California  Alameda County     06001    1898.5     1559308  2022      3   
3  California  Alameda County     06001    1898.5     1559308  2022      4   
4  California  Alameda County     06001    1898.5     1559308  2022      5   

  last_date_time  date_time  last_snap  last_worker  last_disaster  \
0     2021-12-31 2022-01-31          0            0              0   
1     2022-01-28 2022-02-28          0            0              0   
2     2022-02-28 2022-03-31          0           16              0   
3     2022-03-30 2022-04-30          0            0              0   
4     2022-04-30 2022-05-31          0          240              0   

   last_google_calfresh  last_google_food_bank  last_google_food_pantry  \
0                     0                      0                        0   
1                     0                      0                        0   
2                    28                     20                        8   
3                     0                      0                        0   
4                    35                     19                        6   

   last_google_food_stamps  last_google_supplemental  last_google_snap  
0                        0                         0                 0  
1                        0                         0                 0  
2                        2                        10                 0  
3                        0                         0                 0  
4                        2                         5                 0

### Uniform date_time and last_date_time for preparing join

In [15]:
origin_data['date_time'] = origin_data['date_time'] - pd.offsets.MonthBegin(1)

In [16]:
origin_data['last_date_time'] = origin_data['last_date_time'] - pd.offsets.MonthBegin(1)

In [17]:
# create dic to save month and its own data

import collections

lookup = collections.defaultdict()

for i in range(1, 13):
    lookup[i] = origin_data.loc[origin_data.Month == i]

### Adjust Jan table

In [18]:
table_jan = lookup[1]

In [19]:
## fill Jan with 'to_origin_jan_june8'

fillJan = pd.read_excel('to_origin_jan_june8.xlsx', index_col=0,dtype={'fipsValue':str})

In [20]:
col = ['fipsValue', 'numberOfDisaster', 'numberOfWorkers',
       'SNAP_Applications', 'google_calfresh', 'google_food_bank',
       'google_food_pantry', 'google_food_stamps', 'google_supplemental',
       'google_snap']

In [21]:
fillJan = fillJan[col]

In [22]:
fillJan.head()

fipsValue  numberOfDisaster  numberOfWorkers  SNAP_Applications  \
35      06001                 0               20               7427   
71      06003                 0                0                  8   
107     06005                 0                0                171   
143     06007                 0                0               1666   
179     06009                 0                0                213   

     google_calfresh  google_food_bank  google_food_pantry  \
35             54.50             35.75               35.75   
71             66.25             32.50               36.00   
107            66.25             32.50               36.00   
143            66.25             32.50               36.00   
179            66.25             32.50               36.00   

     google_food_stamps  google_supplemental  google_snap  
35                 52.5                48.75            0  
71                 33.0                37.50            0  
107                33.0                37.50            0  
143                33.0                37.50            0  
179                33.0                37.50            0

In [23]:
table_jan.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 312 entries, 0 to 3732
Data columns (total 18 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   State                     312 non-null    object        
 1   County                    312 non-null    object        
 2   fipsValue                 312 non-null    object        
 3   PDensity                  312 non-null    float64       
 4   Population                312 non-null    int64         
 5   Year                      312 non-null    int64         
 6   Month                     312 non-null    int64         
 7   last_date_time            312 non-null    datetime64[ns]
 8   date_time                 312 non-null    datetime64[ns]
 9   last_snap                 312 non-null    int64         
 10  last_worker               312 non-null    int64         
 11  last_disaster             312 non-null    int64         
 12  last_google_calfresh 

In [24]:
table_jan = pd.merge(table_jan, fillJan,on=['fipsValue'], how='left')

In [25]:
table_jan.columns

Index(['State', 'County', 'fipsValue', 'PDensity', 'Population', 'Year',
       'Month', 'last_date_time', 'date_time', 'last_snap', 'last_worker',
       'last_disaster', 'last_google_calfresh', 'last_google_food_bank',
       'last_google_food_pantry', 'last_google_food_stamps',
       'last_google_supplemental', 'last_google_snap', 'numberOfDisaster',
       'numberOfWorkers', 'SNAP_Applications', 'google_calfresh',
       'google_food_bank', 'google_food_pantry', 'google_food_stamps',
       'google_supplemental', 'google_snap'],
      dtype='object')

In [26]:
table_jan

State                  County fipsValue  PDensity  Population  Year  \
0    California          Alameda County     06001    1898.5     1559308  2022   
1    California           Alpine County     06003       1.6        1202  2022   
2    California           Amador County     06005      61.3       37159  2022   
3    California            Butte County     06007     132.1      221578  2022   
4    California        Calaveras County     06009      43.3       44921  2022   
5    California           Colusa County     06011      18.5       21424  2022   
6    California     Contra Costa County     06013    1345.2     1081232  2022   
7    California        Del Norte County     06015      22.8       28066  2022   
8    California        El Dorado County     06017     101.6      181465  2022   
9    California           Fresno County     06019     157.8      948844  2022   
10   California            Glenn County     06021      21.1       28019  2022   
11   California         Humboldt County     06023      33.3      134876  2022   
12   California         Imperial County     06025      39.5      177026  2022   
13   California             Inyo County     06027       1.8       18439  2022   
14   California             Kern County     06029     105.1      857730  2022   
15   California            Kings County     06031     108.8      151390  2022   
16   California             Lake County     06033      48.3       64209  2022   
17   California           Lassen County     06035       7.1       33356  2022   
18   California      Los Angeles County     06037    2099.4     9974203  2022   
19   California           Madera County     06039      70.8      152452  2022   
20   California            Marin County     06041     310.1      256802  2022   
21   California         Mariposa County     06043      12.3       17946  2022   
22   California        Mendocino County     06045      22.6       87612  2022   
23   California           Merced County     06047     132.2      261609  2022   
24   California            Modoc County     06049       2.2        9335  2022   
25   California             Mono County     06051       4.5       14193  2022   
26   California         Monterey County     06053     112.7      424927  2022   
27   California             Napa County     06055     176.6      139253  2022   
28   California           Nevada County     06057     101.3       98606  2022   
29   California           Orange County     06059    3255.4     3086331  2022   
30   California           Placer County     06061     240.6      361518  2022   
31   California           Plumas County     06063       7.4       19286  2022   
32   California        Riverside County     06065     310.4     2266899  2022   
33   California       Sacramento County     06067    1459.0     1450277  2022   
34   California       San Benito County     06069      40.9       56888  2022   
35   California   San Bernardino County     06071     103.4     2078586  2022   
36   California        San Diego County     06073     703.4     3183143  2022   
37   California    San Francisco County     06075    3575.3      829072  2022   
38   California      San Joaquin County     06077     491.4      701050  2022   
39   California  San Luis Obispo County     06079      75.8      274184  2022   
40   California        San Mateo County     06081     998.5      739837  2022   
41   California    Santa Barbara County     06083     113.9      431555  2022   
42   California      Santa Clara County     06085    1412.2     1841569  2022   
43   California       Santa Cruz County     06087     440.1      267203  2022   
44   California           Shasta County     06089      46.4      178520  2022   
45   California           Sierra County     06091       3.1        3019  2022   
46   California         Siskiyou County     06093       7.0       44261  2022   
47   California           Solano County     06095     465.3      421624  2022   
48   California           Sonoma County  

In [27]:
col = ['State', 'County', 'fipsValue', 'PDensity', 'Population', 'Year',
       'Month', 'date_time', 'numberOfDisaster', 'last_date_time',
       'numberOfWorkers', 'SNAP_Applications', 'google_calfresh',
       'google_food_bank', 'google_food_pantry', 'google_food_stamps',
       'google_supplemental']

In [28]:
table_jan = table_jan[col]

In [29]:
table_jan.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 312 entries, 0 to 311
Data columns (total 17 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   State                312 non-null    object        
 1   County               312 non-null    object        
 2   fipsValue            312 non-null    object        
 3   PDensity             312 non-null    float64       
 4   Population           312 non-null    int64         
 5   Year                 312 non-null    int64         
 6   Month                312 non-null    int64         
 7   date_time            312 non-null    datetime64[ns]
 8   numberOfDisaster     312 non-null    int64         
 9   last_date_time       312 non-null    datetime64[ns]
 10  numberOfWorkers      312 non-null    int64         
 11  SNAP_Applications    312 non-null    int64         
 12  google_calfresh      312 non-null    float64       
 13  google_food_bank     312 non-null  

In [30]:
table_jan.rename(columns={'numberOfDisaster':'last_disaster', 'numberOfWorkers':'last_worker', 'SNAP_Applications':'last_snap', 'google_calfresh':'last_google_calfresh',
                         'google_food_bank':'last_google_food_bank', 'google_food_pantry':'last_google_food_pantry', 'google_food_stamps':'last_google_food_stamps',\
                         'google_supplemental':'last_google_supplemental'}, inplace=True)

/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/4138801027.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  table_jan.rename(columns={'numberOfDisaster':'last_disaster', 'numberOfWorkers':'last_worker', 'SNAP_Applications':'last_snap', 'google_calfresh':'last_google_calfresh',


In [31]:
table_jan['last_snap'] = table_jan['last_snap'].clip(lower=0)

/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/1154474909.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  table_jan['last_snap'] = table_jan['last_snap'].clip(lower=0)


In [32]:
table_jan

State                  County fipsValue  PDensity  Population  Year  \
0    California          Alameda County     06001    1898.5     1559308  2022   
1    California           Alpine County     06003       1.6        1202  2022   
2    California           Amador County     06005      61.3       37159  2022   
3    California            Butte County     06007     132.1      221578  2022   
4    California        Calaveras County     06009      43.3       44921  2022   
5    California           Colusa County     06011      18.5       21424  2022   
6    California     Contra Costa County     06013    1345.2     1081232  2022   
7    California        Del Norte County     06015      22.8       28066  2022   
8    California        El Dorado County     06017     101.6      181465  2022   
9    California           Fresno County     06019     157.8      948844  2022   
10   California            Glenn County     06021      21.1       28019  2022   
11   California         Humboldt County     06023      33.3      134876  2022   
12   California         Imperial County     06025      39.5      177026  2022   
13   California             Inyo County     06027       1.8       18439  2022   
14   California             Kern County     06029     105.1      857730  2022   
15   California            Kings County     06031     108.8      151390  2022   
16   California             Lake County     06033      48.3       64209  2022   
17   California           Lassen County     06035       7.1       33356  2022   
18   California      Los Angeles County     06037    2099.4     9974203  2022   
19   California           Madera County     06039      70.8      152452  2022   
20   California            Marin County     06041     310.1      256802  2022   
21   California         Mariposa County     06043      12.3       17946  2022   
22   California        Mendocino County     06045      22.6       87612  2022   
23   California           Merced County     06047     132.2      261609  2022   
24   California            Modoc County     06049       2.2        9335  2022   
25   California             Mono County     06051       4.5       14193  2022   
26   California         Monterey County     06053     112.7      424927  2022   
27   California             Napa County     06055     176.6      139253  2022   
28   California           Nevada County     06057     101.3       98606  2022   
29   California           Orange County     06059    3255.4     3086331  2022   
30   California           Placer County     06061     240.6      361518  2022   
31   California           Plumas County     06063       7.4       19286  2022   
32   California        Riverside County     06065     310.4     2266899  2022   
33   California       Sacramento County     06067    1459.0     1450277  2022   
34   California       San Benito County     06069      40.9       56888  2022   
35   California   San Bernardino County     06071     103.4     2078586  2022   
36   California        San Diego County     06073     703.4     3183143  2022   
37   California    San Francisco County     06075    3575.3      829072  2022   
38   California      San Joaquin County     06077     491.4      701050  2022   
39   California  San Luis Obispo County     06079      75.8      274184  2022   
40   California        San Mateo County     06081     998.5      739837  2022   
41   California    Santa Barbara County     06083     113.9      431555  2022   
42   California      Santa Clara County     06085    1412.2     1841569  2022   
43   California       Santa Cruz County     06087     440.1      267203  2022   
44   California           Shasta County     06089      46.4      178520  2022   
45   California           Sierra County     06091       3.1        3019  2022   
46   California         Siskiyou County     06093       7.0       44261  2022   
47   California           Solano County     06095     465.3      421624  2022   
48   California           Sonoma County  

In [33]:
fx_jan = addFeatures(table_jan)

9


In [34]:
# Build the model for predict
import statsmodels.api as sm
import pandas as pd


features = ['last_snap','last_worker','last_disaster','last_google_calfresh','last_google_food_bank','last_google_food_pantry','last_google_food_stamps','last_google_supplemental','State_California','summer','holiday','PDensity','Population']
target = ['SNAP_Applications']

X = fx_jan[features]
#y = df2[target]
    
# Add constant term to X
X = sm.add_constant(X, has_constant='add')

y_pred = model.predict(X)

# Fit linear regression model
#model = sm.OLS(y, X).fit()

In [35]:
#4. put the y_pred in the first table + set negative value to 0
table_jan['pred_snap'] = y_pred
table_jan['pred_snap'] = table_jan['pred_snap'].clip(lower=0)
    
#update the cur_tabele to its lookup
lookup[1] = table_jan.copy()
table_jan.drop(columns='last_snap', inplace=True)
table_jan.rename(columns={'pred_snap':'last_snap'}, inplace=True)


/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/2088968259.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  table_jan['pred_snap'] = y_pred
/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/2088968259.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  table_jan['pred_snap'] = table_jan['pred_snap'].clip(lower=0)
/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/2088968259.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Da

In [36]:
col = ['date_time', 'last_snap','fipsValue']
table_jan = table_jan[col]
table_jan.rename(columns={'date_time':'last_date_time'}, inplace=True)

/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/1929522037.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  table_jan.rename(columns={'date_time':'last_date_time'}, inplace=True)


In [37]:
table_feb = lookup[2]

In [38]:
table_feb

State                  County fipsValue  PDensity  Population  \
1     California          Alameda County     06001    1898.5     1559308   
13    California           Alpine County     06003       1.6        1202   
25    California           Amador County     06005      61.3       37159   
37    California            Butte County     06007     132.1      221578   
49    California        Calaveras County     06009      43.3       44921   
61    California           Colusa County     06011      18.5       21424   
73    California     Contra Costa County     06013    1345.2     1081232   
85    California        Del Norte County     06015      22.8       28066   
97    California        El Dorado County     06017     101.6      181465   
109   California           Fresno County     06019     157.8      948844   
121   California            Glenn County     06021      21.1       28019   
133   California         Humboldt County     06023      33.3      134876   
145   California         Imperial County     06025      39.5      177026   
157   California             Inyo County     06027       1.8       18439   
169   California             Kern County     06029     105.1      857730   
181   California            Kings County     06031     108.8      151390   
193   California             Lake County     06033      48.3       64209   
205   California           Lassen County     06035       7.1       33356   
217   California      Los Angeles County     06037    2099.4     9974203   
229   California           Madera County     06039      70.8      152452   
241   California            Marin County     06041     310.1      256802   
253   California         Mariposa County     06043      12.3       17946   
265   California        Mendocino County     06045      22.6       87612   
277   California           Merced County     06047     132.2      261609   
289   California            Modoc County     06049       2.2        9335   
301   California             Mono County     06051       4.5       14193   
313   California         Monterey County     06053     112.7      424927   
325   California             Napa County     06055     176.6      139253   
337   California           Nevada County     06057     101.3       98606   
349   California           Orange County     06059    3255.4     3086331   
361   California           Placer County     06061     240.6      361518   
373   California           Plumas County     06063       7.4       19286   
385   California        Riverside County     06065     310.4     2266899   
397   California       Sacramento County     06067    1459.0     1450277   
409   California       San Benito County     06069      40.9       56888   
421   California   San Bernardino County     06071     103.4     2078586   
433   California        San Diego County     06073     703.4     3183143   
445   California    San Francisco County     06075    3575.3      829072   
457   California      San Joaquin County     06077     491.4      701050   
469   California  San Luis Obispo County     06079      75.8      274184   
481   California        San Mateo County     06081     998.5      739837   
493   California    Santa Barbara County     06083     113.9      431555   
505   California      Santa Clara County     06085    1412.2     1841569   
517   California       Santa Cruz County     06087     440.1      267203   
529   California           Shasta County     06089      46.4      178520   
541   California           Sierra County     06091       3.1        3019   
553   California         Siskiyou County     06093       7.0       44261   
565   California           Solano County     06095     465.3      421624   
577   California           Sonoma County     06097     278.2      491790   
589   California       Stanislaus County     06099     345.2      522794   
601   California           Sutter County     06101     156.2       95067   
613   California           Tehama County     06103      21.

In [39]:
## Feb

table_feb = lookup[2]
table_feb.drop(columns='last_snap', inplace=True)
table_feb = pd.merge(table_feb, table_jan, on=['last_date_time', 'fipsValue'], how='left' )

# 1. predict y in feb
fx_feb = addFeatures(table_feb)
X = fx_feb[features]
X = sm.add_constant(X, has_constant='add')
y_pred = model.predict(X)

# 2. put the y_pred in the first table
table_feb['pred_snap'] = y_pred
table_feb['pred_snap'] = table_feb['pred_snap'].clip(lower=0)
lookup[2] = table_feb.copy()
table_feb.drop(columns='last_snap', inplace=True)
table_feb.rename(columns={'pred_snap':'last_snap'}, inplace=True)

# 3. extract ['date_time', 'last_snap','fipsValue'] to join March table and rename it 
table_feb = table_feb[col]
table_feb.rename(columns={'date_time':'last_date_time'}, inplace=True)


7


/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/2213125864.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  table_feb.drop(columns='last_snap', inplace=True)


In [40]:
lookup[2]

State                  County fipsValue  PDensity  Population  Year  \
0    California          Alameda County     06001    1898.5     1559308  2022   
1    California           Alpine County     06003       1.6        1202  2022   
2    California           Amador County     06005      61.3       37159  2022   
3    California            Butte County     06007     132.1      221578  2022   
4    California        Calaveras County     06009      43.3       44921  2022   
5    California           Colusa County     06011      18.5       21424  2022   
6    California     Contra Costa County     06013    1345.2     1081232  2022   
7    California        Del Norte County     06015      22.8       28066  2022   
8    California        El Dorado County     06017     101.6      181465  2022   
9    California           Fresno County     06019     157.8      948844  2022   
10   California            Glenn County     06021      21.1       28019  2022   
11   California         Humboldt County     06023      33.3      134876  2022   
12   California         Imperial County     06025      39.5      177026  2022   
13   California             Inyo County     06027       1.8       18439  2022   
14   California             Kern County     06029     105.1      857730  2022   
15   California            Kings County     06031     108.8      151390  2022   
16   California             Lake County     06033      48.3       64209  2022   
17   California           Lassen County     06035       7.1       33356  2022   
18   California      Los Angeles County     06037    2099.4     9974203  2022   
19   California           Madera County     06039      70.8      152452  2022   
20   California            Marin County     06041     310.1      256802  2022   
21   California         Mariposa County     06043      12.3       17946  2022   
22   California        Mendocino County     06045      22.6       87612  2022   
23   California           Merced County     06047     132.2      261609  2022   
24   California            Modoc County     06049       2.2        9335  2022   
25   California             Mono County     06051       4.5       14193  2022   
26   California         Monterey County     06053     112.7      424927  2022   
27   California             Napa County     06055     176.6      139253  2022   
28   California           Nevada County     06057     101.3       98606  2022   
29   California           Orange County     06059    3255.4     3086331  2022   
30   California           Placer County     06061     240.6      361518  2022   
31   California           Plumas County     06063       7.4       19286  2022   
32   California        Riverside County     06065     310.4     2266899  2022   
33   California       Sacramento County     06067    1459.0     1450277  2022   
34   California       San Benito County     06069      40.9       56888  2022   
35   California   San Bernardino County     06071     103.4     2078586  2022   
36   California        San Diego County     06073     703.4     3183143  2022   
37   California    San Francisco County     06075    3575.3      829072  2022   
38   California      San Joaquin County     06077     491.4      701050  2022   
39   California  San Luis Obispo County     06079      75.8      274184  2022   
40   California        San Mateo County     06081     998.5      739837  2022   
41   California    Santa Barbara County     06083     113.9      431555  2022   
42   California      Santa Clara County     06085    1412.2     1841569  2022   
43   California       Santa Cruz County     06087     440.1      267203  2022   
44   California           Shasta County     06089      46.4      178520  2022   
45   California           Sierra County     06091       3.1        3019  2022   
46   California         Siskiyou County     06093       7.0       44261  2022   
47   California           Solano County     06095     465.3      421624  2022   
48   California           Sonoma County  

In [41]:
table_feb

last_date_time     last_snap fipsValue
0       2022-02-01   8820.468173     06001
1       2022-02-01     43.324065     06003
2       2022-02-01    131.616366     06005
3       2022-02-01   1393.318589     06007
4       2022-02-01    156.070461     06009
5       2022-02-01     95.891423     06011
6       2022-02-01   5419.832838     06013
7       2022-02-01    113.375858     06015
8       2022-02-01    843.027942     06017
9       2022-02-01   6386.231433     06019
10      2022-02-01    113.543728     06021
11      2022-02-01    878.932914     06023
12      2022-02-01   1048.892856     06025
13      2022-02-01     90.612865     06027
14      2022-02-01   5837.792742     06029
15      2022-02-01    506.371901     06031
16      2022-02-01    355.504463     06033
17      2022-02-01    130.641443     06035
18      2022-02-01  61992.554747     06037
19      2022-02-01    847.177161     06039
20      2022-02-01   1169.164638     06041
21      2022-02-01     87.425505     06043
22      2022-02-01    518.228174     06045
23      2022-02-01   1757.414579     06047
24      2022-02-01     65.548212     06049
25      2022-02-01     78.484024     06051
26      2022-02-01   2715.079671     06053
27      2022-02-01    621.016315     06055
28      2022-02-01    425.750443     06057
29      2022-02-01  16415.211173     06059
30      2022-02-01   1721.590199     06061
31      2022-02-01     91.960233     06063
32      2022-02-01  14583.981258     06065
33      2022-02-01   9166.106755     06067
34      2022-02-01    232.665874     06069
35      2022-02-01  13652.921190     06071
36      2022-02-01  19493.285615     06073
37      2022-02-01   3865.913846     06075
38      2022-02-01   4375.198504     06077
39      2022-02-01   1452.247170     06079
40      2022-02-01   3584.451848     06081
41      2022-02-01   2597.677126     06083
42      2022-02-01   9162.061291     06085
43      2022-02-01   1346.031429     06087
44      2022-02-01   1199.154907     06089
45      2022-02-01     48.050613     06091
46      2022-02-01    187.166256     06093
47      2022-02-01   2302.780414     06095
48      2022-02-01   2624.110509     06097
49      2022-02-01   3297.524529     06099
50      2022-02-01    435.822938     06101
51      2022-02-01    305.794031     06103
52      2022-02-01     76.674989     06105
53      2022-02-01   3152.531656     06107
54      2022-02-01    220.247135     06109
55      2022-02-01   4465.284831     06111
56      2022-02-01   1276.909114     06113
57      2022-02-01    375.722015     06115
58      2022-02-01    603.592656     48001
59      2022-02-01    381.446641     48003
60      2022-02-01    811.375287     48005
61      2022-02-01    417.337062     48007
62      2022-02-01    297.058393     48009
63      2022-02-01    258.521507     48011
64      2022-02-01    607.582599     48013
65      2022-02-01    435.127407     48015
66      2022-02-01    289.064670     48017
67      2022-02-01    401.081101     48019
68      2022-02-01    830.972246     48021
69      2022-02-01    271.021971     48023
70      2022-02-01    475.235601     48025
71      2022-02-01   2673.847673     48027
72      2022-02-01  13023.420816     48029
73      2022-02-01    331.545091     48031
74      2022-02-01    280.713698     48033
75      2022-02-01    351.982974     48035
76      2022-02-01    857.261143     48037
77      2022-02-01   2372.168834     48039
78      2022-02-01   1501.568470     48041
79      2022-02-01    332.511527     48043
80      2022-02-01    257.178207     48045
81      2022-02-01    329.540928     48047
82      2022-02-01    519.457774     48049
83      2022-02-01    337.780252     48051
84      2022-02-01    543.373069     48053
85      2022-02-01    546.968499     48055
86      2022-02-01    402.920863     48057
87      2022-02-01    334.182515     48059
88      2022-02-01   3025.245339     48061
89      2022-02-01    315.272633     48063
90      2022-02-01    466.957052     48065
91      2022-02-01    447.606115     48067
92   

In [42]:
for i in range(3, 13):
    
    if i == 3:
        last_table = table_feb
    
    #1. get the first table from dict

    cur_table = lookup[i]
    cur_table.drop(columns='last_snap', inplace=True)

    #2. merge first table with last_snap from previous table
    cur_table = pd.merge(cur_table, last_table, on=['last_date_time', 'fipsValue'], how='left' )
    cur_table.info()
    #3. predict y in cur_table
    fx = addFeatures(cur_table)
    fx.info()
    X = fx[features]
    X = sm.add_constant(X,has_constant='add')
    y_pred = model.predict(X)

    #4. put the y_pred in the first table + set negative value to 0
    cur_table['pred_snap'] = y_pred
    cur_table['pred_snap'] = cur_table['pred_snap'].clip(lower=0)
    
    #update the cur_tabele to its lookup
    lookup[i] = cur_table.copy()
    cur_table.drop(columns='last_snap', inplace=True)
    cur_table.rename(columns={'pred_snap':'last_snap'}, inplace=True)
    
    #5. extract['date_time', 'last_snap','fipsValue'] to join March table and rename it
    last_table = cur_table[col]
    last_table.rename(columns={'date_time':'last_date_time'}, inplace=True)
    
    print('    ')
    print('    ')
    print('------Finied------')
    print(str(i))



/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cur_table.drop(columns='last_snap', inplace=True)
/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  last_table.rename(columns={'date_time':'last_date_time'}, inplace=True)
/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/sta

<class 'pandas.core.frame.DataFrame'>
Int64Index: 312 entries, 0 to 311
Data columns (total 18 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   State                     312 non-null    object        
 1   County                    312 non-null    object        
 2   fipsValue                 312 non-null    object        
 3   PDensity                  312 non-null    float64       
 4   Population                312 non-null    int64         
 5   Year                      312 non-null    int64         
 6   Month                     312 non-null    int64         
 7   last_date_time            312 non-null    datetime64[ns]
 8   date_time                 312 non-null    datetime64[ns]
 9   last_worker               312 non-null    int64         
 10  last_disaster             312 non-null    int64         
 11  last_google_calfresh      312 non-null    int64         
 12  last_google_food_bank 

/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  last_table.rename(columns={'date_time':'last_date_time'}, inplace=True)
/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cur_table.drop(columns='last_snap', inplace=True)
/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/st

    
    
------Finied------
5
<class 'pandas.core.frame.DataFrame'>
Int64Index: 312 entries, 0 to 311
Data columns (total 18 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   State                     312 non-null    object        
 1   County                    312 non-null    object        
 2   fipsValue                 312 non-null    object        
 3   PDensity                  312 non-null    float64       
 4   Population                312 non-null    int64         
 5   Year                      312 non-null    int64         
 6   Month                     312 non-null    int64         
 7   last_date_time            312 non-null    datetime64[ns]
 8   date_time                 312 non-null    datetime64[ns]
 9   last_worker               312 non-null    int64         
 10  last_disaster             312 non-null    int64         
 11  last_google_calfresh      312 non-null    int64      

/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  last_table.rename(columns={'date_time':'last_date_time'}, inplace=True)
/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cur_table.drop(columns='last_snap', inplace=True)
/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/st

<class 'pandas.core.frame.DataFrame'>
Int64Index: 312 entries, 0 to 311
Data columns (total 20 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   State                     312 non-null    object        
 1   County                    312 non-null    object        
 2   fipsValue                 312 non-null    object        
 3   PDensity                  312 non-null    float64       
 4   Population                312 non-null    int64         
 5   Year                      312 non-null    int64         
 6   Month                     312 non-null    int64         
 7   last_date_time            312 non-null    datetime64[ns]
 8   date_time                 312 non-null    datetime64[ns]
 9   last_worker               312 non-null    int64         
 10  last_disaster             312 non-null    int64         
 11  last_google_calfresh      312 non-null    int64         
 12  last_google_food_bank 

    
    
------Finied------
12


/var/folders/gh/67px3m710b74y6c1mwgnkcq40000gn/T/ipykernel_8415/284806640.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  last_table.rename(columns={'date_time':'last_date_time'}, inplace=True)


In [43]:
cur_table.head()

State            County fipsValue  PDensity  Population  Year  Month  \
0  California    Alameda County     06001    1898.5     1559308  2022     12   
1  California     Alpine County     06003       1.6        1202  2022     12   
2  California     Amador County     06005      61.3       37159  2022     12   
3  California      Butte County     06007     132.1      221578  2022     12   
4  California  Calaveras County     06009      43.3       44921  2022     12   

  last_date_time  date_time  last_worker  last_disaster  last_google_calfresh  \
0     2022-11-01 2022-12-01          259              0                    29   
1     2022-11-01 2022-12-01            0              0                    58   
2     2022-11-01 2022-12-01            0              0                    58   
3     2022-11-01 2022-12-01            0              0                    58   
4     2022-11-01 2022-12-01            0              0                    58   

   last_google_food_bank  last_google_food_pantry  last_google_food_stamps  \
0                     30                       12                        4   
1                     34                       11                        4   
2                     34                       11                        4   
3                     34                       11                        4   
4                     34                       11                        4   

   last_google_supplemental  last_google_snap    last_snap  
0                        11                 0  9676.184973  
1                        19                 0     0.000000  
2                        19                 0    25.826390  
3                        19                 0  1232.431643  
4                        19                 0    77.624113

In [44]:
last_table.head()

last_date_time    last_snap fipsValue
0     2022-12-01  9676.184973     06001
1     2022-12-01     0.000000     06003
2     2022-12-01    25.826390     06005
3     2022-12-01  1232.431643     06007
4     2022-12-01    77.624113     06009

In [45]:
pd.concat([lookup[2], lookup[3]]).info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 624 entries, 0 to 311
Data columns (total 19 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   State                     624 non-null    object        
 1   County                    624 non-null    object        
 2   fipsValue                 624 non-null    object        
 3   PDensity                  624 non-null    float64       
 4   Population                624 non-null    int64         
 5   Year                      624 non-null    int64         
 6   Month                     624 non-null    int64         
 7   last_date_time            624 non-null    datetime64[ns]
 8   date_time                 624 non-null    datetime64[ns]
 9   last_worker               624 non-null    int64         
 10  last_disaster             624 non-null    int64         
 11  last_google_calfresh      624 non-null    int64         
 12  last_google_food_bank 

In [46]:
for i in range(1, 13):
    if 'last_google_snap' in lookup[i].columns.tolist():
        lookup[i] = lookup[i].drop('last_google_snap', axis=1)

In [47]:
df = lookup[1]

for i in range(2, 13):
    df = pd.concat([df, lookup[i]])

In [48]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3744 entries, 0 to 311
Data columns (total 18 columns):
 #   Column                    Non-Null Count  Dtype         
---  ------                    --------------  -----         
 0   State                     3744 non-null   object        
 1   County                    3744 non-null   object        
 2   fipsValue                 3744 non-null   object        
 3   PDensity                  3744 non-null   float64       
 4   Population                3744 non-null   int64         
 5   Year                      3744 non-null   int64         
 6   Month                     3744 non-null   int64         
 7   date_time                 3744 non-null   datetime64[ns]
 8   last_disaster             3744 non-null   int64         
 9   last_date_time            3744 non-null   datetime64[ns]
 10  last_worker               3744 non-null   int64         
 11  last_snap                 3744 non-null   float64       
 12  last_google_calfresh 

In [49]:
df.head()

State            County fipsValue  PDensity  Population  Year  Month  \
0  California    Alameda County     06001    1898.5     1559308  2022      1   
1  California     Alpine County     06003       1.6        1202  2022      1   
2  California     Amador County     06005      61.3       37159  2022      1   
3  California      Butte County     06007     132.1      221578  2022      1   
4  California  Calaveras County     06009      43.3       44921  2022      1   

   date_time  last_disaster last_date_time  last_worker  last_snap  \
0 2022-01-01              0     2021-12-01           20     7427.0   
1 2022-01-01              0     2021-12-01            0        8.0   
2 2022-01-01              0     2021-12-01            0      171.0   
3 2022-01-01              0     2021-12-01            0     1666.0   
4 2022-01-01              0     2021-12-01            0      213.0   

   last_google_calfresh  last_google_food_bank  last_google_food_pantry  \
0                 54.50                  35.75                    35.75   
1                 66.25                  32.50                    36.00   
2                 66.25                  32.50                    36.00   
3                 66.25                  32.50                    36.00   
4                 66.25                  32.50                    36.00   

   last_google_food_stamps  last_google_supplemental    pred_snap  
0                     52.5                     48.75  8142.327049  
1                     33.0                     37.50     0.000000  
2                     33.0                     37.50     0.000000  
3                     33.0                     37.50  1294.071226  
4                     33.0                     37.50     0.000000

In [50]:
keep = df.copy()

### Adjust for Dashboard Json_Jun 9

-  add one variable ['snap_per_capita']
-  add one variable ['flag']

#### Add snap_per_capita

In [51]:
# drop rows whose last_snap is 0

# Drop rows with 0 in column'snap_change_ratio'
df = df.drop(df.loc[(df['last_snap'] == 0)].index)

df['snap_per_capita'] = round((df.pred_snap / df.last_snap),3)

df.head()

State               County fipsValue  PDensity  Population  Year  \
0  California       Alameda County     06001    1898.5     1559308  2022   
3  California         Butte County     06007     132.1      221578  2022   
6  California  Contra Costa County     06013    1345.2     1081232  2022   
8  California     El Dorado County     06017     101.6      181465  2022   
9  California        Fresno County     06019     157.8      948844  2022   

   Month  date_time  last_disaster last_date_time  last_worker  last_snap  \
0      1 2022-01-01              0     2021-12-01           20     7427.0   
3      1 2022-01-01              0     2021-12-01            0     1666.0   
6      1 2022-01-01              0     2021-12-01          391     3337.0   
8      1 2022-01-01              0     2021-12-01            0      577.0   
9      1 2022-01-01              0     2021-12-01          186     6867.0   

   last_google_calfresh  last_google_food_bank  last_google_food_pantry  \
0                 54.50                  35.75                    35.75   
3                 66.25                  32.50                    36.00   
6                 54.50                  35.75                    35.75   
8                 66.25                  32.50                    36.00   
9                 66.25                  32.50                    36.00   

   last_google_food_stamps  last_google_supplemental    pred_snap  \
0                     52.5                     48.75  8142.327049   
3                     33.0                     37.50  1294.071226   
6                     52.5                     48.75  4459.891941   
8                     33.0                     37.50   543.184081   
9                     33.0                     37.50  6351.882350   

   snap_per_capita  
0            1.096  
3            0.777  
6            1.336  
8            0.941  
9            0.925

#### Add Flag

#### 1. For each county, calculate the mean and standard deviation for "snap per capita" across all data we have.

In [52]:
gp = df.groupby(['State','County'])['snap_per_capita']

df1 = gp.agg({'mean','std'}).reset_index().rename(columns={'mean':'mean_snap_per_capita',
                                                          'std':'std_snap_per_capita'})

df1.head()

State               County  mean_snap_per_capita  std_snap_per_capita
0  California       Alameda County              1.022917             0.033757
1  California         Butte County              0.981333             0.111672
2  California  Contra Costa County              1.064417             0.105508
3  California     El Dorado County              1.066417             0.187122
4  California        Fresno County              0.991000             0.028123

In [53]:
df1['Yellow_flag'] = abs(df1.mean_snap_per_capita + df1.std_snap_per_capita)
df1['Red_flag'] = abs(df1.mean_snap_per_capita + 2*df1.std_snap_per_capita)

#### 2. Use mean + std dev for yellow and mean + 2*std dev for red but do this for the absolute values calculated by county above.

In [54]:
df1.head()

State               County  mean_snap_per_capita  std_snap_per_capita  \
0  California       Alameda County              1.022917             0.033757   
1  California         Butte County              0.981333             0.111672   
2  California  Contra Costa County              1.064417             0.105508   
3  California     El Dorado County              1.066417             0.187122   
4  California        Fresno County              0.991000             0.028123   

   Yellow_flag  Red_flag  
0     1.056674  1.090431  
1     1.093005  1.204677  
2     1.169924  1.275432  
3     1.253539  1.440662  
4     1.019123  1.047246

In [55]:
# create a dict to lookup yellow and red flag for each county
# (State, County) : [yellow_value, red_value]
import collections

lookup = collections.defaultdict(list)

for i in range(len(df1)):
    state_key = df1.iloc[i,0]
    county_key = df1.iloc[i, 1]
    yellow = df1.iloc[i, -2]
    red = df1.iloc[i, -1]
    lookup[(state_key, county_key)] = [yellow, red]

In [56]:
df.head()

State               County fipsValue  PDensity  Population  Year  \
0  California       Alameda County     06001    1898.5     1559308  2022   
3  California         Butte County     06007     132.1      221578  2022   
6  California  Contra Costa County     06013    1345.2     1081232  2022   
8  California     El Dorado County     06017     101.6      181465  2022   
9  California        Fresno County     06019     157.8      948844  2022   

   Month  date_time  last_disaster last_date_time  last_worker  last_snap  \
0      1 2022-01-01              0     2021-12-01           20     7427.0   
3      1 2022-01-01              0     2021-12-01            0     1666.0   
6      1 2022-01-01              0     2021-12-01          391     3337.0   
8      1 2022-01-01              0     2021-12-01            0      577.0   
9      1 2022-01-01              0     2021-12-01          186     6867.0   

   last_google_calfresh  last_google_food_bank  last_google_food_pantry  \
0                 54.50                  35.75                    35.75   
3                 66.25                  32.50                    36.00   
6                 54.50                  35.75                    35.75   
8                 66.25                  32.50                    36.00   
9                 66.25                  32.50                    36.00   

   last_google_food_stamps  last_google_supplemental    pred_snap  \
0                     52.5                     48.75  8142.327049   
3                     33.0                     37.50  1294.071226   
6                     52.5                     48.75  4459.891941   
8                     33.0                     37.50   543.184081   
9                     33.0                     37.50  6351.882350   

   snap_per_capita  
0            1.096  
3            0.777  
6            1.336  
8            0.941  
9            0.925

In [57]:
# flag county in df by the value in the lookup

# add one empty column for df
df['Flag'] = ''

# fill 'Flag' in df by the value in the lookup
for i in range(len(df)):
    state_key = df.iloc[i,0]
    county_key = df.iloc[i, 1]
    yellow = lookup[(state_key, county_key)][0]
    red = lookup[(state_key, county_key)][1]
    
    # check the value of snap_per_capita; idx = -2 cuz add one new column
    if df.iloc[i, -2] > red:
        df.iloc[i, -1] = 'Red'
    elif (df.iloc[i, -2] <= red) and (df.iloc[i, -2] > yellow):
        df.iloc[i, -1] = 'Yellow'
    else:
        df.iloc[i, -1] = 'Green'

In [58]:
df.head()

State               County fipsValue  PDensity  Population  Year  \
0  California       Alameda County     06001    1898.5     1559308  2022   
3  California         Butte County     06007     132.1      221578  2022   
6  California  Contra Costa County     06013    1345.2     1081232  2022   
8  California     El Dorado County     06017     101.6      181465  2022   
9  California        Fresno County     06019     157.8      948844  2022   

   Month  date_time  last_disaster last_date_time  last_worker  last_snap  \
0      1 2022-01-01              0     2021-12-01           20     7427.0   
3      1 2022-01-01              0     2021-12-01            0     1666.0   
6      1 2022-01-01              0     2021-12-01          391     3337.0   
8      1 2022-01-01              0     2021-12-01            0      577.0   
9      1 2022-01-01              0     2021-12-01          186     6867.0   

   last_google_calfresh  last_google_food_bank  last_google_food_pantry  \
0                 54.50                  35.75                    35.75   
3                 66.25                  32.50                    36.00   
6                 54.50                  35.75                    35.75   
8                 66.25                  32.50                    36.00   
9                 66.25                  32.50                    36.00   

   last_google_food_stamps  last_google_supplemental    pred_snap  \
0                     52.5                     48.75  8142.327049   
3                     33.0                     37.50  1294.071226   
6                     52.5                     48.75  4459.891941   
8                     33.0                     37.50   543.184081   
9                     33.0                     37.50  6351.882350   

   snap_per_capita   Flag  
0            1.096    Red  
3            0.777  Green  
6            1.336    Red  
8            0.941  Green  
9            0.925  Green

In [59]:
### Create a json file - June 9

col = df.columns.to_list()
col.remove('snap_per_capita')
col.remove('date_time')
col.remove('last_date_time')

df_json = df[col]
df_json = df_json.to_dict(orient='records')

In [60]:
df_json

[{'State': 'California',
  'County': 'Alameda County',
  'fipsValue': '06001',
  'PDensity': 1898.5,
  'Population': 1559308,
  'Year': 2022,
  'Month': 1,
  'last_disaster': 0,
  'last_worker': 20,
  'last_snap': 7427.0,
  'last_google_calfresh': 54.5,
  'last_google_food_bank': 35.75,
  'last_google_food_pantry': 35.75,
  'last_google_food_stamps': 52.5,
  'last_google_supplemental': 48.75,
  'pred_snap': 8142.327049361177,
  'Flag': 'Red'},
 {'State': 'California',
  'County': 'Butte County',
  'fipsValue': '06007',
  'PDensity': 132.1,
  'Population': 221578,
  'Year': 2022,
  'Month': 1,
  'last_disaster': 0,
  'last_worker': 0,
  'last_snap': 1666.0,
  'last_google_calfresh': 66.25,
  'last_google_food_bank': 32.5,
  'last_google_food_pantry': 36.0,
  'last_google_food_stamps': 33.0,
  'last_google_supplemental': 37.5,
  'pred_snap': 1294.0712259693746,
  'Flag': 'Green'},
 {'State': 'California',
  'County': 'Contra Costa County',
  'fipsValue': '06013',
  'PDensity': 1345.2,
  

In [61]:
import json

json_file = 'pred_databaseForFunction_dashboard_2022.json'

with open(json_file, 'w') as file:
    json.dump(df_json, file)

In [62]:
# review json file

with open(json_file, 'r') as file:
    data = json.load(file)

# Dump the data to a formatted JSON string
formatted_json = json.dumps(data, indent=4, sort_keys=True)


In [63]:
print(formatted_json)

[
    {
        "County": "Alameda County",
        "Flag": "Red",
        "Month": 1,
        "PDensity": 1898.5,
        "Population": 1559308,
        "State": "California",
        "Year": 2022,
        "fipsValue": "06001",
        "last_disaster": 0,
        "last_google_calfresh": 54.5,
        "last_google_food_bank": 35.75,
        "last_google_food_pantry": 35.75,
        "last_google_food_stamps": 52.5,
        "last_google_supplemental": 48.75,
        "last_snap": 7427.0,
        "last_worker": 20,
        "pred_snap": 8142.327049361177
    },
    {
        "County": "Butte County",
        "Flag": "Green",
        "Month": 1,
        "PDensity": 132.1,
        "Population": 221578,
        "State": "California",
        "Year": 2022,
        "fipsValue": "06007",
        "last_disaster": 0,
        "last_google_calfresh": 66.25,
        "last_google_food_bank": 32.5,
        "last_google_food_pantry": 36.0,
        "last_google_food_stamps": 33.0,
        "last_google_sup